In [2]:
#from transformers import BertTokenizer, BertForMaskedLM
import torch
from torch.optim import Adam

In [2]:
#tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
#model = BertForMaskedLM.from_pretrained('bert-base-uncased')

#text = ("After Abraham Lincoln won the November 1860 presidential "
#        "election on an anti-slavery platform, an initial seven "
#        "slave states declared their secession from the country "
#        "to form the Confederacy. War broke out in April 1861 "
#        "when secessionist forces attacked Fort Sumter in South "
#        "Carolina, just over a month after Lincoln's "
#        "inauguration.")

In [3]:
#inputs = tokenizer(text, return_tensors='pt')


In [4]:
#inputs.keys()


In [5]:
#inputs


In [6]:
#inputs['labels'] = inputs.input_ids.detach().clone()

In [7]:
#inputs

In [8]:
# create random array of floats in equal dimension to input_ids
#rand = torch.rand(inputs.input_ids.shape)
# where the random array is less than 0.15, we set true
#mask_arr = rand < 0.15
#mask_arr

In [9]:
#(inputs.input_ids != 101) * (inputs.input_ids != 102)

In [10]:
#mask_arr = (rand < 0.15) * (inputs.input_ids != 101) * (inputs.input_ids != 102)
#mask_arr

In [11]:
# create selection from mask_arr
#selection = torch.flatten((mask_arr[0]).nonzero()).tolist()
#selection

In [12]:
# apply selection index to inputs.input_ids, adding MASK tokens
#inputs.input_ids[0, selection] = 103

In [13]:
#inputs

## UTILS

In [5]:
from matplotlib import pyplot

## MODEL


# from VGAE https://github.com/DaehanKim/vgae_pytorch

In [14]:
#'model/epoch_'+ str(epoch) +'_' + str(sum(epoch_loss) / len(epoch_loss)) + '__'

## DATA

In [2]:
import os
import pickle
import torch

class Vocab(object):

    def __init__(self, filename='', load=False, threshold=5):
        if load:
            assert os.path.exists(filename), "Vocab file does not exist at " + filename

            self.id2word, self.word2id = self.load(filename)
            self.size = len(self.id2word)
            self.threshold = threshold
            self.wordCounter = None
        else:
            self.id2word, self.word2id = {}, {}
            self.size = 0
            self.threshold = threshold
            # We always add some custom tokens into the vocabulary.
            self.add_words(
                {'<PAD>': 6, '<UNK>': 6,'<MSK>' : 6,'pad' : 6})
        self.word_embed = None

    def add_words(self, counterOfTokens):
        for item, value in counterOfTokens.items():
            if value >= self.threshold:
                if item not in self.word2id:
                    # add it to the vocab
                    self.word2id[item] = self.size
                    self.id2word[self.size] = item
                    self.size += 1

    def load(self, filename):
        with open(filename, 'rb') as infile:
            
            fi = pickle.load(infile)
            #fi = {k: fi[k] for k in list(fi)[:8000]}
            id2word = fi
            word2id = {word:id for id, word in id2word.items()}
            self.id2word, self.word2id = id2word, word2id
            self.size = len(self.id2word)

        return id2word, word2id

    def save(self, filename):
        if os.path.exists(filename):
            os.remove(filename)
           
        with open(filename, 'wb') as outfile:
            pickle.dump(self.id2word, outfile)

    def __len__(self):
        return self.size


    def init_word_embed(self, cfg, cache_dir='datasets/.word_vectors_cache'):
        if cfg['word_vectors'] == 'Word2Vec':
            from torchnlp.word_to_vector import FastText
            all_word_vector = FastText(language=cfg['language'], cache=cache_dir, aligned=True)
        else:
            raise NotImplementedError('No word_vectors found which are called {}.'.format(cfg['word_vectors']))

        # The the vectors only correspond to lower character words:
        all_words = [word.lower() for word in list(self.word2id.keys())]
        weights = all_word_vector[all_words]
        
        word_embed = torch.nn.Embedding(*weights.shape, _weight=weights)
        #if cfg['device'] == 'cuda':
        #    word_embed.cuda()

        self.word_embed = word_embed
        self.embed_size = weights.shape[1]

    def words2vecs(self, words: list):
        if not self.word_embed:
            raise AttributeError("The word embeddings aren't initialized yet.")
        else:
            vecs = self.word_embed(torch.tensor(self.map(words), requires_grad=False))
        return vecs

    def one_hot_ids2vecs(self, ids):
        vecs = self.word_embed(ids)
        return vecs

    def map(self, token_list):
        """
        Map a list of tokens to their ids.
        """
        return [self.word2id[w] if w in self.word2id else self.word2id['<UNK>'] for w in token_list]

    def unmap(self, idx_list):
        """
        Unmap ids back to tokens.
        """
        return [self.id2word[idx] for idx in idx_list]
    
def get_pos_vocab():
    """
    Function to set up a part of speech vocabulary handcrafed.
    """
    pos_id2word = {0: '<PAD>', 1: '<UNK>', 2: 'DET', 3: 'PROPN', 4: 'VERB', 5: 'PART', 6: 'ADJ', 7: 'PUNCT', 8: 'CCONJ',
                   9: 'ADP', 10: 'PRON', 11: 'NOUN', 12: 'ADV', 13: 'INTJ', 14: 'NUM', 15: 'X', 16: 'SYM'}
    pos_word2id = {word: id for id, word in pos_id2word.items()}
    pos_vocab = Vocab()
    pos_vocab.id2word = pos_id2word
    pos_vocab.word2id = pos_word2id
    pos_vocab.size = len(pos_vocab.id2word)
    
    return pos_vocab


In [3]:
# Code to load sst data
from torch.utils.data import Dataset
import torch
import numpy as np


class SSTData(Dataset):
    def __init__(self,
                 sst_data,
                 vocab,
                 nlp,
                 lemma_vocab,
                 pos_vocab = None,
                 self_loop=True):

        self.lemma_vocab = lemma_vocab
        self.self_loop = self_loop
        
        
        #sst_data = [sample for sample in sst_data if sample['label'] != 'neutral']
        self.sst_data = sst_data
        #self.sentiment_vocab = {'negative': 0, 'positive': 1}
        
        # Add sentencizer in the nlp if not already in it:
        if "sentencizer" not in nlp.pipe_names:
            # sentencizer = nlp.create_pipe("sentencizer")
            nlp.add_pipe('sentencizer', first=True)
        self.nlp = nlp

        self.vocab = vocab
        if pos_vocab is None:
            self.pos_vocab = get_pos_vocab()
        else:
            self.pos_vocab = pos_vocab

    def __getitem__(self, idx):
        txt = self.sst_data[idx]
        if len(txt.split()) <64:
            txt = txt + ' PAD'*(64-len(txt.split()))  
        elif len(txt.split()) > 64:
            tmp = txt.split()
            txt = ' '.join(tmp[:64])
        doc = self.nlp(txt)
        #print(len(txt.split()), len(doc))
        token_ids = self.vocab.map([token.text for token in doc])
        # create random array of floats in equal dimension to input_ids
        rand = torch.rand(np.shape(token_ids))
        # where the random array is less than 0.15, we set true
        mask_arr = rand < 0.15
        # create selection from mask_arr
        selection = torch.flatten((mask_arr).nonzero()).tolist()
        #if len(selection) >= 1:
        #    label = [token_ids[selection[0]]]
        #else:
        #    label = [0 ]
        for i in selection: 
            token_ids[i] = 2
            break
            
            
        
        # make lambda
        adj, root_id = doc_to_adj(doc, directed=False, self_loop=self.self_loop)

        lamb = adj

        # normalize
        denom = lamb.sum(1)
        lamb /= denom

        # make text indices
        
        
        # make pos ids
        pos_ids = self.pos_vocab.map([token.pos_ for token in doc])
        for idx,token in enumerate(doc):
            if token.text == 'PAD':
                pos_ids[idx] = 1
        for i in selection: 
            pos_ids[i] = 1
            break

        # make lemma ids
        lemma_ids = self.lemma_vocab.map([token.lemma_ for token in doc])
        for idx,val in enumerate(lemma_ids): 
            if val == 7364:
                lemma_ids[idx] = 1
        for i in selection: 
            lemma_ids[i] = 2
            break
        # make label
        label = self.vocab.map([token.text for token in doc])
        
        return token_ids[:64], pos_ids[:64], lamb[:64,:64], label[:64], root_id, lemma_ids[:64]

    
    def data_check(self):
        for idx,sent in enumerate(self.sst_data):
            if len(sent) < 10:
                self.sst_data.remove(sent)
            
    def __len__(self):
        return len(self.sst_data)



In [4]:

def collate_fn_sentim(batch):
    lens = []
    for sample in batch:
        text, pos, lamb, label, root_id, lemma = sample[:6]
        lens.append(lamb.shape[1])

    max_len = max(lens)
    lambs = []
    texts = []
    poss = []
    lemmas = []
    labels = []
    root_ids = []
    for sample in batch:
        text, pos, lamb, label, root_id, lemma = sample[:6]
        # Big lamb
        lamb_ = torch.zeros(1, max_len, max_len)
        lamb_[0, :lamb.shape[0], :lamb.shape[1]] = lamb
        lambs.append(lamb_)

        # Big text
        text_ = torch.zeros(1, max_len, dtype=torch.long)
        text_[0, :len(text)] = torch.tensor(text)
        texts.append(text_)

        # Big pos
        pos_ = torch.zeros(1, max_len, dtype=torch.long)
        pos_[0, :len(pos)] = torch.tensor(pos)
        poss.append(pos_)

        # Big lemma
        lemma_ = torch.zeros(1, max_len, dtype=torch.long)
        lemma_[0, :len(lemma)] = torch.tensor(lemma)
        lemmas.append(lemma_)

        # Big label:
        label_ = torch.zeros(1, max_len, dtype=torch.long)
        label_[0, :len(label)] = torch.tensor(label)
        labels.append(label_)

        # Big root_id:
        root_id_ = torch.ones(1) * root_id
        root_ids.append(root_id_.long())

    lambs = torch.cat(lambs, dim=0)
    texts = torch.cat(texts, dim=0)
    poss = torch.cat(poss, dim=0)
    labels = torch.cat(labels, dim=0)
    root_ids = torch.cat(root_ids, dim=0)
    lemmas = torch.cat(lemmas, dim=0)

    return lambs, poss, texts, labels, lens, root_ids, lemmas


In [5]:


def doc_to_adj(sent, directed=True, self_loop=False):
    # Sent should be a spacy document. Can also be longer than a sentence.
    sent_len = len(sent)
    root_id = 1
    ret = torch.zeros(sent_len, sent_len, dtype=torch.float32)

    for token in sent:
        for child in token.children:
            if child.i >= sent_len:
                #print('Something goes wrong here.')
                print(child.i, sent_len, sent, token.i, token)
                pass
            ret[token.i, child.i] = 1
        if token.dep_ == 'ROOT':
            root_id = token.i

    if not directed:
        ret = ret + ret.transpose(0, 1)

    if self_loop:
        for i in range(sent_len):
            ret[i, i] = 1
        
    return ret, root_id



In [6]:
#from sklearn.metrics import f1_score, precision_score, recall_score, accuracy_score
from tqdm import tqdm

from torchnlp.datasets import smt_dataset
from torchtext.datasets import WikiText103
import click

import spacy

import json
import os
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import numpy as np
from collections import Counter


In [7]:
cfg = {"repo_name": "saved_models/sst_model1+/", 
       "epochs": 50, "optimizer": "adam", 
       "cuda": True, 
       "lr": 0.0002, 
       "num_of_layer": 3, 
       "hidden_dimension": 10, 
       "batch_size": 1,
       "word_vectors": "Word2Vec",
       "bias": False, 
       "pos_emb_dim": 30,
       "model_type": "gcn",
       "data_amount": 1.0, 
       "data_set": "sst", 
       "word_emb_dim": 70,
       "lemma_emb_dim": 50, 
       "trainerfilename": "saved_models/sst_model1+/",
       "logfilename": "saved_models/sst_model1+/log.txt",
       "num_of_classes": 64,
       "language": "en",
       "normalize_lamb": True,
       "laplacian": False,
       "input_dimension": 300,
       'load_model' : False}

In [8]:
from pathlib import Path
import re
train_data = Path('datasets/wikitext-103/wiki.train.tokens').read_text(encoding='utf-8')
val_data = Path('datasets/wikitext-103/wiki.valid.tokens').read_text(encoding='utf-8')
test_data = Path('datasets/wikitext-103/wiki.test.tokens').read_text(encoding='utf-8')

In [9]:
train_data = train_data.lower()
val_data = val_data.lower()
test_data = test_data.lower()

In [10]:
heading_pattern = '( \n \n = [^=]*[^=] = \n \n )'

In [11]:
# Split out train headings and articles
train_split = re.split(heading_pattern, train_data)
train_headings = [x[7:-7] for x in train_split[1::2]]
train_articles = [x for x in train_split[2::2]]

# Split out validation headings and articles
val_split = re.split(heading_pattern, val_data)
val_headings = [x[7:-7] for x in val_split[1::2]]
val_articles = [x for x in val_split[2::2]]

# Split out test headings and articles
test_split = re.split(heading_pattern, test_data)
test_headings = [x[7:-7] for x in test_split[1::2]]
test_articles = [x for x in test_split[2::2]]



In [12]:
train_data = [i.split('. ') for i in train_articles]
val_data = [i.split('. ') for i in val_articles]
test_data = [i.split('. ') for i in test_articles]

In [13]:
test_data = [item for sublist in test_data for item in sublist]
val_data = [item for sublist in val_data for item in sublist]
train_data = [item for sublist in train_data for item in sublist]

In [14]:
data_amount = 0.001

print('Loading data...')
nlp = spacy.load('en_core_web_sm')
cw = Counter()
cl = Counter()



train_set, test_set = train_data, test_data

# only use the the percentage of data we want:
train_set = train_set[:int(len(train_set) * data_amount)]
#test_set = test_set[:int(len(test_set) * data_amount)]




Loading data...


In [15]:
len(test_set)

9368

In [16]:
tm = Vocab()
tm.word2id

{'<PAD>': 0, '<UNK>': 1, '<MSK>': 2, 'pad': 3}

In [17]:
# # # Count words:
# for sample in train_set + test_set: cw += Counter([token.text for token in nlp(sample)])
# # # Count lemma:
# for sample in train_set + test_set: cl += Counter([token.lemma_ for token in nlp(sample)])

# vocab = Vocab()
# lemma_vocab = Vocab()


# # # prepare vocab
# vocab.add_words(cw)
# # #cfg['input_dimension'] = 300

# lemma_vocab.add_words(cl)
# pos_vocab = get_pos_vocab()

# # Save the parameter:
# #with open(repo_name + 'config.json', 'w') as fp:
# #    json.dump(cfg.get_as_dict(), fp)

In [18]:
vocab = Vocab()
lemma_vocab = Vocab()
vocab.load('word_vocab_500.json')
lemma_vocab.load('lemma_vocab_500.json')

({0: '<PAD>',
  1: '<UNK>',
  2: 'the',
  3: 'Tower',
  4: 'Building',
  5: 'of',
  6: 'Little',
  7: 'Rock',
  8: 'Arsenal',
  9: ',',
  10: 'also',
  11: 'know',
  12: 'as',
  13: 'U.S',
  14: 'be',
  15: 'a',
  16: 'building',
  17: 'locate',
  18: 'in',
  19: 'MacArthur',
  20: 'Park',
  21: 'downtown',
  22: 'Arkansas',
  23: 'build',
  24: '1840',
  25: 'it',
  26: 'part',
  27: "'s",
  28: 'first',
  29: 'military',
  30: 'installation',
  31: 'since',
  32: 'its',
  33: 'have',
  34: 'house',
  35: 'two',
  36: 'museum',
  37: 'home',
  38: 'to',
  39: 'Museum',
  40: 'Natural',
  41: 'History',
  42: 'and',
  43: 'from',
  44: '1942',
  45: '1997',
  46: 'Military',
  47: '2001',
  48: 'headquarters',
  49: 'Club',
  50: '1894',
  51: '\n ',
  52: 'receive',
  53: 'name',
  54: 'distinct',
  55: 'tower',
  56: 'besides',
  57: 'last',
  58: 'structure',
  59: 'original',
  60: 'one',
  61: 'old',
  62: 'central',
  63: 'General',
  64: 'Douglas',
  65: 'who',
  66: 'become',
 

In [19]:
vocab.unmap([0,1,2,3,4,5,6])

['<PAD>', '<UNK>', 'The', 'Tower', 'Building', 'of', 'the']

In [20]:
print('Prepare data ...')


train_data = SSTData(
    train_set,
    vocab,
    nlp,
    lemma_vocab,
)
test_data = SSTData(
    test_set,
    vocab,
    nlp,
    lemma_vocab,
)

cfg['vocab'] = vocab
cfg['pos_vocab'] = get_pos_vocab()
cfg['lemma_vocab'] = lemma_vocab


Prepare data ...


In [21]:
ps = get_pos_vocab()

In [22]:
ps.unmap([1])

['<UNK>']

In [23]:
train_data.__len__()/32

121.46875

In [24]:
train_data.data_check()

In [25]:
train_data.__len__()

3825

In [26]:
test_data.__len__()

9368

In [27]:
collate_fn = collate_fn_sentim

train_loader = DataLoader(train_data,
                          batch_size=32,
                          collate_fn=collate_fn,
                         drop_last=True)

test_loader = DataLoader(test_data,
                         batch_size=32,
                         collate_fn=collate_fn,
                        drop_last=True)


In [28]:
#lambs, poss, texts, labels, lens, root_ids, lemmas

In [29]:
for i, batch in enumerate(train_loader):
    print(batch[6][30])
    break

tensor([   2,   93,   14,   60,    5,    2,  302,    1,    5,   29,  158,   18,
           2, 9319,    1,   42,   14,  303,   38,   14,    2,  304,    2,    5,
           2,   87,   88,   89,  306,  307,  308,  259,   43,    2,  103,    1,
           1,    1,    1,    1,    1,    1,    1,    1,    1,    1,    1,    1,
           1,    1,    1,    1,    1,    1,    1,    1,    1,    1,    1,    1,
           1,    1,    1,    1])


In [30]:
vocab.__len__()

13234

In [31]:
vocab.unmap([0,1,2,3,4,5,6,7])

['<PAD>', '<UNK>', 'The', 'Tower', 'Building', 'of', 'the', 'Little']

In [32]:
train_set[:10]

['the tower building of the little rock arsenal , also known as u.s',
 'arsenal building , is a building located in macarthur park in downtown little rock , arkansas ',
 "built in 1840 , it was part of little rock 's first military installation ",
 'since its decommissioning , the tower building has housed two museums ',
 'it was home to the arkansas museum of natural history and antiquities from 1942 to 1997 and the macarthur museum of arkansas military history since 2001 ',
 'it has also been the headquarters of the little rock æsthetic club since 1894 ',
 '\n the building receives its name from its distinct octagonal tower ',
 'besides being the last remaining structure of the original little rock arsenal and one of the oldest buildings in central arkansas , it was also the birthplace of general douglas macarthur , who became the supreme commander of us forces in the south pacific during world war ii ',
 'it was also the starting place of the camden expedition ',
 'in 2011 it was na

In [33]:
"""
Utility functions for torch.
"""

import click, ast, torch
#import matplotlib.pyplot as plt

### torch specific functions
def get_optimizer(name, parameters, lr, l2=0):
    if name == 'sgd':
        return torch.optim.SGD(parameters, lr=lr, weight_decay=l2)
    elif name == 'adam':
        return torch.optim.Adam(parameters, weight_decay=l2) # use default lr
    elif name == 'adamax':
        return torch.optim.Adamax(parameters, weight_decay=l2) # use default lr
    elif name == 'adadelta':
        return torch.optim.Adadelta(parameters, lr=lr, weight_decay=l2)
    else:
        raise Exception("Unsupported optimizer: {}".format(name))


def visualize_performance(performance, repo_name, show=False):
    plt.figure(figsize=(15, 10))

    # accuracy
    ax = plt.subplot(3, 2, 1)
    ax.set_title('Accuracy')
    ax.plot(performance['acc_test'], label='test')
    ax.plot(performance['acc_train'], label='train')

    ax.set_ylim([0.5, 1])
    ax.set_ylabel('%')
    ax.set_xlabel('epoch')
    plt.legend()

    # precision
    ax = plt.subplot(3, 2, 2)
    ax.set_title('Precision')
    ax.plot(performance['prec_test'], label='test')
    ax.plot(performance['prec_train'], label='train')

    ax.set_ylim([.5, 1])
    ax.set_ylabel('%')
    ax.set_xlabel('epoch')
    plt.legend()

    # recall
    ax = plt.subplot(3, 2, 3)
    ax.set_title('Recall')
    ax.plot(performance['recall_test'], label='test')
    ax.plot(performance['recall_train'], label='train')

    ax.set_ylim([.5, 1])
    ax.set_ylabel('%')
    ax.set_xlabel('epoch')
    plt.legend()

    # f1
    ax = plt.subplot(3, 2, 4)
    ax.set_title('F1')
    ax.plot(performance['f1_test'], label='test')
    ax.plot(performance['f1_train'], label='train')

    ax.set_ylim([.5, 1])
    ax.set_ylabel('%')
    ax.set_xlabel('epoch')
    plt.legend()

    # loss
    ax = plt.subplot(3, 1, 3)
    ax.set_title('loss')
    ax.plot(performance['loss'])

    ax.set_ylim([0, 0.5])
    ax.set_ylabel('loss')
    ax.set_xlabel('')

    plt.subplots_adjust(top=0.92, bottom=0.08, left=0.10, right=0.95, hspace=0.35,
                        wspace=0.35)

    if not show:
        plt.savefig(repo_name + 'performance_vis.png')
    else:
        plt.show()

    plt.close()


class PythonLiteralOption(click.Option):
    def type_cast_value(self, ctx, value):
        # Either we denote a range, or a list with precise samples:
        # 1) Range:
        if 'range' in value:
            idx_open = value.find('(')
            idx_close = value.find(')')
            # Get the range input
            range_input = value[idx_open + 1:idx_close].split(',')
            # Make it to numbers:
            range_input = [int(num) for num in range_input]
            try :
                return list(range(*range_input))
            except:
                raise click.BadParameter(value)
        else:
            try:
                return ast.literal_eval(value)
            except:
                raise click.BadParameter(value)


In [34]:
import torch.nn as nn
import torch.nn.functional as F


class VGAE(nn.Module):
	def __init__(self):
		super(VGAE,self).__init__()
        #encoder
		self.base_gcn = GraphConvSparse(input_dim, hidden1_dim, activation=F.relu)
		self.batchnorm_1 = nn.BatchNorm1d(hidden1_dim)
		self.base2_gcn = GraphConvSparse(hidden1_dim, hidden2_dim, activation=F.relu)
		self.batchnorm_2 = nn.BatchNorm1d(hidden2_dim)
		#self.gcn_mean = GraphConvSparse(hidden2_dim, hidden3_dim, activation=lambda x:x)
		#self.gcn_logstddev = GraphConvSparse(hidden2_dim, hidden3_dim, activation=lambda x:x)
		self.linear_1_enc = nn.Linear(hidden2_dim*max_len,hidden3_dim)
		self.gcn_mean = nn.Linear(hidden3_dim, hidden4_dim)
		self.gcn_logstddev = nn.Linear(hidden3_dim, hidden4_dim)
		self.N = torch.distributions.Normal(0, 1)
		self.N.loc = self.N.loc.cuda() # hack to get sampling on the GPU
		self.N.scale = self.N.scale.cuda()
        
        
        
        #decoder
		self.linear_0_dec =  nn.Linear(hidden4_dim , hidden3_dim)
		self.linear_1_dec =  nn.Linear(hidden3_dim , hidden2_dim*max_len)
		self.unflatten = nn.Unflatten(dim=0, unflattened_size=(max_len, hidden2_dim))
		self.dec_1 = GraphConvSparse(hidden2_dim, hidden1_dim, activation=F.relu)
		self.batchnorm_3 = nn.BatchNorm1d(hidden1_dim)
		self.dec_2 = GraphConvSparse(hidden1_dim, output_dim, activation=F.log_softmax)
		#self.dec_3 = GraphConvSparse(hidden1_dim, output_dim, activation=F.log_softmax)
		#self.linear_2_dec =  nn.Linear(input_dim*64 , hidden1_linear)
		#self.act1 = nn.ReLU()
		#self.linear_3_dec =  nn.Linear(hidden1_linear , hidden2_linear)
		#self.act2 = nn.ReLU()
		#self.linear_4_dec =  nn.Linear(hidden2_linear , output_dim) 
		self.act_output = nn.LogSoftmax()
		self.kl = 0
        
        
	def encode(self, X,adj):
		hidden = F.dropout(F.relu(self.base_gcn(X,adj)),p=0.2)
		hidden = self.batchnorm_1(hidden)
		hidden = F.dropout(F.relu(self.base2_gcn(hidden,adj)),0.2)
		hidden = self.batchnorm_2(hidden)
		hidden = torch.flatten(hidden)
		hidden = F.relu(self.linear_1_enc(hidden))
		self.mean = self.gcn_mean(hidden)
		self.logstd = self.gcn_logstddev(hidden)
		#self.mean = self.gcn_mean(hidden,adj)
		#self.logstd = self.gcn_logstddev(hidden,adj)
		#print(self.mean,self.logstd)
		gaussian_noise = self.N.sample(self.mean.shape)
		sampled_z = gaussian_noise*torch.exp(self.logstd) + self.mean
		self.kl = (1 + 2*self.logstd - self.mean**2 - torch.exp(self.logstd)**2).sum(0)
		#print(self.logstd,self.mean)
		return sampled_z
    
	def decode(self,Z,adj):
		A_pred = F.relu(self.linear_0_dec(Z))
		A_pred = F.relu(self.linear_1_dec(A_pred))
		A_pred = self.unflatten(A_pred)
		A_pred = F.dropout(F.relu(self.dec_1(A_pred,adj)),0.2)
		A_pred = self.batchnorm_3(A_pred)
		A_pred = F.log_softmax(self.dec_2(A_pred,adj),dim = 1)
		#A_pred = self.dec_3(A_pred,adj)
		#A_pred = torch.flatten(A_pred)
		
		#A_pred = self.linear_2_dec(A_pred)
		#print(A_pred)
		#A_pred = self.act1(A_pred)
		#A_pred = F.dropout(self.linear_3_dec(A_pred),0.2)
		#A_pred = self.act2(A_pred)
		#A_pred = self.linear_4_dec(A_pred)
		return A_pred

	def forward(self, X,adj):
		Z = self.encode(X,adj)
		A_pred = self.decode(Z,adj)
		return A_pred

class GraphConvSparse(nn.Module):
	def __init__(self, input_dim, output_dim, activation = F.relu, **kwargs):
		super(GraphConvSparse, self).__init__(**kwargs)
		self.weight = glorot_init(input_dim, output_dim) 
		self.activation = activation

	def forward(self, inputs, adj):
		x = inputs
		x = torch.mm(x,self.weight)
		#print(adj,x)
		x = torch.mm(adj, x)
		#print(x)
		#outputs = self.activation(x)
		return x





def glorot_init(input_dim, output_dim):
	init_range = np.sqrt(6.0/(input_dim + output_dim))
	initial = torch.rand(input_dim, output_dim)*2*init_range - init_range
	return nn.Parameter(initial)


class GAE(nn.Module):
	def __init__(self,input_dim, hidden1_dim,hidden2_dim):
		super(GAE,self).__init__()
		self.base_gcn = GraphConvSparse(input_dim, hidden1_dim)
		self.gcn_mean = GraphConvSparse(hidden1_dim, hidden2_dim, activation=lambda x:x)

	def encode(self, X):
		hidden = self.base_gcn(X)
		z = self.mean = self.gcn_mean(hidden)
		return z

	def forward(self, X):
		Z = self.encode(X)
		A_pred = dot_product_decode(Z)
		return A_pred

In [35]:
# import torch.nn as nn
# import torch.nn.functional as F

# class VGAE(nn.Module):
# 	def __init__(self):
# 		super(VGAE,self).__init__()
# 		self.base_gcn = GraphConvSparse(input_dim, hidden1_dim, activation=F.relu)
# 		self.base2_gcn = GraphConvSparse(hidden1_dim, hidden2_dim, activation=F.relu)
# 		self.gcn_mean = GraphConvSparse(hidden2_dim, hidden4_dim, activation=None)
# 		self.gcn_logstddev = GraphConvSparse(hidden2_dim, hidden4_dim, activation=None)
# 		self.dec_1 = GraphConvSparse(hidden4_dim, hidden2_dim, activation=F.relu)
# 		self.dec_2 = GraphConvSparse(hidden2_dim, hidden1_dim, activation=F.relu)
# 		self.dec_3 = GraphConvSparse(hidden1_dim, input_dim, activation=F.relu)
# 		self.linear_2_dec =  nn.Linear(input_dim*64 , hidden1_linear)
# 		self.act1 = nn.ReLU()
# 		self.linear_3_dec =  nn.Linear(hidden1_linear , hidden2_linear)
# 		self.act2 = nn.ReLU()
# 		self.linear_4_dec =  nn.Linear(hidden2_linear , output_dim) 
# 		self.act_output = nn.LogSoftmax()
# 		self.kl = 0
        
        
# 	def encode(self, X,adj):
# 		hidden = self.base_gcn(X,adj)
# 		hidden = self.base2_gcn(hidden,adj)
# 		self.mean = self.gcn_mean(hidden,adj)
# 		self.logstd = self.gcn_logstddev(hidden,adj)
# 		gaussian_noise = torch.randn(X.size(0), hidden4_dim).cuda()
# 		sampled_z = gaussian_noise*torch.exp(self.logstd) + self.mean
# 		self.kl = 0.5*(1 + 2*self.logstd - self.mean**2 - torch.exp(self.logstd)**2).sum(1).mean()
# 		#print(sampled_z.size())
# 		return sampled_z
    
# 	def decode(self,Z,adj):
# 		A_pred = self.dec_1(Z,adj)
# 		A_pred = self.dec_2(A_pred,adj)
# 		A_pred = self.dec_3(A_pred,adj)
# 		A_pred = torch.flatten(A_pred)
		
# 		A_pred = self.linear_2_dec(A_pred)
# 		#print(A_pred)
# 		A_pred = self.act1(A_pred)
# 		A_pred = F.dropout(self.linear_3_dec(A_pred),0.2)
# 		A_pred = self.act2(A_pred)
# 		A_pred = self.linear_4_dec(A_pred)
# 		#print(A_pred)
# 		return self.act_output(A_pred)
# 		return A_pred

# 	def forward(self, X,adj):
# 		Z = self.encode(X,adj)
# 		A_pred = self.decode(Z,adj)
# 		return A_pred

# class GraphConvSparse(nn.Module):
# 	def __init__(self, input_dim, output_dim, activation = F.relu, **kwargs):
# 		super(GraphConvSparse, self).__init__(**kwargs)
# 		self.weight = glorot_init(input_dim, output_dim) 
# 		self.activation = activation

# 	def forward(self, inputs, adj):
# 		x = inputs
# 		x = torch.mm(x,self.weight)
# 		x = torch.mm(adj, x)
# 		if self.activation:
# 			outputs = self.activation(x)
# 			return outputs
# 		return x




# def glorot_init(input_dim, output_dim):
# 	init_range = np.sqrt(6.0/(input_dim + output_dim))
# 	initial = torch.rand(input_dim, output_dim)*2*init_range - init_range
# 	return nn.Parameter(initial)


# class GAE(nn.Module):
# 	def __init__(self,input_dim, hidden1_dim,hidden2_dim):
# 		super(GAE,self).__init__()
# 		self.base_gcn = GraphConvSparse(input_dim, hidden1_dim)
# 		self.gcn_mean = GraphConvSparse(hidden1_dim, hidden2_dim, activation=lambda x:x)

# 	def encode(self, X):
# 		hidden = self.base_gcn(X)
# 		z = self.mean = self.gcn_mean(hidden)
# 		return z

# 	def forward(self, X):
# 		Z = self.encode(X)
# 		A_pred = dot_product_decode(Z)
# 		return A_pred

In [36]:
input_dim = 450
hidden1_dim = 512
hidden2_dim = 256
hidden3_dim = 2048
hidden4_dim = 100
hidden1_linear= 1024
hidden2_linear = 2048
output_dim = 13234
use_feature = True
num_epoch = 3
learning_rate = 0.00001
batch_size = 32
max_len = 64

In [37]:
import torch
import torch.nn as nn
from torch.autograd import Variable


import json


def unpack_batch(batch, cuda):
    if cuda:
        inputs = [Variable(b.cuda()) for b in batch[:10]]
        labels = Variable(batch[10].cuda())
    else:
        inputs = [Variable(b) for b in batch[:10]]
        labels = Variable(batch[10])

    # To have the possibility to pass custom adjacency matrix and words vectors to the prediction.
    inputs += [None, None]  # It will be referenced as [cust_adj, cust_words]
    tokens = batch[0]
    head = batch[5]
    subj_pos = batch[6]
    obj_pos = batch[7]
    lens = batch[1].eq(0).long().sum(1).squeeze()

    return inputs, labels, tokens, head, subj_pos, obj_pos, lens


# A helping function.
def make_eyes(lambs, lens):
    eyes = torch.zeros(lambs.shape)
    for i, le in enumerate(lens):
        eyes[i,:le, :le] = torch.eye(le)
    return eyes


class MLM:
    def __init__(self, cfg, cuda=False):
        # First check if we load the model:
        if cfg['load_model']:
            assert 'repo_name' in cfg, 'We need a file name to load the model.'
            # Get all hyperparameter:
            cfg.update(json.load(open(cfg['repo_name'] + 'config.json', 'r')))
            # Set cuda:
            cfg['cuda'] = cuda
            self.cuda = cuda
            checkpoint = torch.load(cfg['repo_name'] + 'model_params.pt', map_location=torch.device('cpu'))

            # just get the vocab dimensions:
            cfg['vocab_len'] = checkpoint['embedding']['weight'].shape[0]
            cfg['pos_vocab_len'] = checkpoint['pos_embedding']['weight'].shape[0]
            cfg['lemma_vocab_len'] = checkpoint['lemma_embedding']['weight'].shape[0]
            # don't need the checkpoints anymmore
            del checkpoint

            # Vocab initialisation:
            self.vocab = Vocab()
            self.pos_vocab = Vocab()
            self.lemma_vocab = Vocab()

            # make random model initialization:
            self.random_model_init_(cfg)

            # load pretrainded weights:
            self.load(cfg['repo_name'], cuda=cfg['cuda'])

        else:
            # Set cuda:
            cfg['cuda'] = cuda
            self.cuda = cuda

            # We need the vocabs given in cfg:
            self.vocab = cfg['vocab']
            self.pos_vocab = cfg['pos_vocab']
            self.lemma_vocab = cfg['lemma_vocab']

            # set up necessary vocab lens:
            cfg['vocab_len'] = len(self.vocab)
            cfg['pos_vocab_len'] = len(self.pos_vocab)
            cfg['lemma_vocab_len'] = len(self.lemma_vocab)

            # init parameter:
            self.random_model_init_(cfg)

            if self.vocab.word_embed is None: self.vocab.init_word_embed(cfg)
            self.embedding = self.vocab.word_embed


        self.model_type = cfg['model_type']
        self.new_model = True

        if self.cuda:
            self.model.cuda()
            #self.output_layer.cuda()
            self.embedding.cuda()
            #self.first_layer.cuda()
            #self.last_layer.cuda()
            self.pos_embedding.cuda()
            self.word_embedding.cuda()
            self.lemma_embedding.cuda()

        # Init optimizer:
        #params = list(self.model.parameters()) \
        #         + list(self.pos_embedding.parameters()) \
        #         + list(self.word_embedding.parameters()) \
        #         + list(self.lemma_embedding.parameters())
                # + list(self.first_layer.parameters()) \
                # + list(self.last_layer.parameters()) \
                # + list(self.output_layer.parameters()) \

        #self.optim = get_optimizer(cfg['optimizer'],
        #                                         params,
        #                                         cfg['lr'])

        self.loss = nn.CrossEntropyLoss()

    def random_model_init_(self, cfg):
        assert all(x in cfg for x in ['vocab_len', 'pos_vocab_len',
                                      'lemma_vocab_len']), 'Please indicate the dimensions of the vocabularies.'
        
        # Embedding layer:
        self.embedding = nn.Embedding(cfg['vocab_len'], cfg['input_dimension'])

        # Trainable word embedding
        self.word_embedding = nn.Embedding(cfg['vocab_len'], cfg['word_emb_dim'])
        with torch.no_grad(): self.word_embedding.weight[0] = 0. # set '<PAD>' to zero
        self.word_embedding.weight = nn.parameter.Parameter(self.word_embedding.weight, requires_grad=True) 
        # Make it to leaf variable again

        # Pos embedding layer
        self.pos_embedding = nn.Embedding(cfg['pos_vocab_len'], cfg['pos_emb_dim'])
        with torch.no_grad(): self.pos_embedding.weight[0] = 0. # set '<PAD>' to zero
        self.pos_embedding.weight = nn.parameter.Parameter(self.pos_embedding.weight, requires_grad=True)

        # lemma embedding laayer
        self.lemma_embedding = nn.Embedding(cfg['lemma_vocab_len'], cfg['lemma_emb_dim'])
        with torch.no_grad(): self.lemma_embedding.weight[0] = 0. # set '<PAD>' to zero
        self.lemma_embedding.weight = nn.parameter.Parameter(self.lemma_embedding.weight, requires_grad=True)
        
        # Add a first layer if wanted:
        
        #self.first_layer = GCNModel(num_of_layer=1,
        #                    input_dimension=cfg['input_dimension'] + cfg['pos_emb_dim'] + cfg[
         #                       'word_emb_dim'] + cfg['lemma_emb_dim'],
         #                   hidden_dimension=cfg['hidden_dimension'],
         #                   bias=cfg['bias'])
        #print(cfg['input_dimension'] + cfg['pos_emb_dim'] + 
        #                         cfg['word_emb_dim'] + cfg['lemma_emb_dim'])
        self.model = VGAE()
        
        params = list(self.model.parameters()) \
                 + list(self.word_embedding.parameters()) \
                 + list(self.pos_embedding.parameters()) \
                 + list(self.lemma_embedding.parameters()) \
                  
        
        self.optim = Adam(params, lr=learning_rate,weight_decay=0.1)

        # Set up the model:
        #self.mp_model = GCNModel(num_of_layer=cfg['num_of_layer'],
        #                         input_dimension=cfg['hidden_dimension'],
        #                         hidden_dimension=cfg['hidden_dimension'],
        #                         bias=cfg['bias']
         #                        )

        # Last layer
        #self.last_layer = GCNModel(num_of_layer=1,
        #                           input_dimension=cfg['hidden_dimension'],
         #                          hidden_dimension=cfg['hidden_dimension'],
          #                         bias=cfg['bias'])
        # Output layer:

        #self.output_layer = nn.Linear(cfg['hidden_dimension'],
        #                              cfg['num_of_classes'],
        #                              bias=cfg['bias'])

    def update(self, batch):
        # Free the optimizer:
        #self.optim.zero_grad()
        # Unwrap batch
        batch_loss = []
        batch_kl = []
        batch_ce = []
        
        lambs, poss, texts, labels, lens, _, lemmas = batch[:7]
        #lambs = lambs.to(torch.int64)
            # Adjacency in the first matrix are identity matrices:
            #eyes = make_eyes(lambs, lens)
            # Set on cuda:
        if self.cuda:
            lambs = lambs.cuda()
            texts = texts.cuda()
            labels = labels.cuda()
            #eyes = eyes.cuda()
            poss = poss.cuda()
            lemmas = lemmas.cuda()
        #print(np.shape(poss))
            # Propagate through the the model
            # Embedding layers
        
            

        

        #print(np.shape(x))
        #print(np.shape(lambs))
        

        #labels = labels[0]
        #print(labels)
        self.optim.zero_grad()
        
        #print(np.shape(x),np.shape(lambs))
        for sample in range(len(batch[0])):
            

            
            const_word_vec = self.embedding(texts)
            word_vec = self.word_embedding(texts)
            pos_vec = self.pos_embedding(poss)
            lemma_vec = self.lemma_embedding(lemmas)



            
            #x = torch.cat([texts, poss, lemmas], dim=0).transpose(0,1)

           # print(texts[:5],poss[:5],lemmas[:5],x[:5])
            x = torch.cat([word_vec, pos_vec,const_word_vec, lemma_vec], dim=2)
            #x_min, _ = torch.min(x[sample], dim=1, keepdim=True)
            #x_max, _ = torch.max(x[sample], dim=1, keepdim=True)
            #x[sample] = (x[sample] - x_min) / (x_max - x_min) # Broadcasting rules apply
            #print(x[sample])
            #print(np.shape(x))
            #x = x[0]
            #x = x.float()
            #print(x[0])
            #lambs = lambs.float()
            #print(np.shape(lambs))
            #try:
            A_pred = self.model(x[sample],lambs[sample])
            #print(x[sample])
            #print(np.shape(A_pred))
            #print(np.shape(labels))
            
            #const_word_vec_lab = self.embedding(labels)
            #word_vec_lab = self.word_embedding(labels)
            #pos_vec_lab = self.pos_embedding(poss)

            #lemma_ve_lab = self.lemma_embedding(lemmas)
            #labels_concat = torch.cat([word_vec_lab, pos_vec_lab,const_word_vec_lab, lemma_ve_lab], dim=2)
            
            #labels_concat_min, _ = torch.min(labels_concat[sample], dim=1, keepdim=True)
            #labels_concat_max, _ = torch.max(labels_concat[sample], dim=1, keepdim=True)
            #labels_concat[sample] = (labels_concat[sample] - labels_concat_min) / (labels_concat_max - labels_concat_min) # Broadcasting rules apply
            #norm = lambs.shape[0] * lambs.shape[0] / float((lambs.shape[0] * lambs.shape[0] - lambs.sum()) * 2)
            #for i in A_pred[0]:
            #    print(i)
            #print(labels_concat[sample])
            
            lab_idx = 0
            for idx,val in enumerate(texts[sample]):
                if val == 2:
                    lab_idx = idx
            
            #lab = [0]*output_dim
            #lab[labels[sample][0]] = 1
            #lab = torch.FloatTensor(lab).cuda()
            #print('labels : ',labels[sample][lab_idx])
            #print('pred : ',A_pred[lab_idx][labels[sample][lab_idx]])
            loss_ce =  F.nll_loss(A_pred[lab_idx],labels[sample][lab_idx])
            #print('loss : ', loss)
            
            #kl loss from gpt
            #kl_divergence = 0.5*torch.sum(1 + self.model.logstd - self.model.mean.pow(2) - self.model.logstd.exp())
            #print(self.model.logstd)
            #print(self.model.mean)

            #loss from vgae paper
            #kl_divergence = 0.5* (1 + 2*self.model.logstd - self.model.mean**2 - torch.exp(self.model.logstd)**2).sum(1).mean()
            #kl = 0
            #if self.model.kl < -100:
            #    kl = -100
            #else:
            kl = self.model.kl
            loss = loss_ce - kl 
            #print('loss_ce : ', loss_ce)
            #print('kl :', kl)
            
            loss.backward()
            
            self.optim.step()
            
            #if loss < 2000 and loss > -2000:
            batch_loss.append(float(loss.detach()))
            batch_kl.append(float(kl))
            batch_ce.append(float(loss_ce.detach()))
            #print('avg_loss = ',sum(batch_loss) / len(batch_loss))
            #print('KLD : ',kl_divergence)
            #print ('lgstd, meansq, logstdexp', self.model.logstd, self.model.mean.pow(2), self.model.logstd.exp())
            #except:
            #    print('weird thing happening')
            #    pass
           
            
        #print('loss : ', loss)
        #loss_mse = nn.MSELoss()
        #output_mse = loss_mse(A_pred.view(-1), labels.view(-1))
        #output_mse.backward()
        #self.optim.step()
        # last layer:
        #x = self.last_layer(x, eyes)

        # Mean pooling: We expect xTs is of shape (batch_size, seq_len, hidden_dim)
        #x = x.sum(1) / x.shape[1]

        # Propagate through the last layer:
        #x = self.output_layer(x)

        # x.shape should be (batch_size, num_of_classes).
        # label.shape should be (batch_size).
        
        #loss_val = self.loss(x, labels.to(torch.float32))

        # Do the backward step:
        #loss_val.backward()

        # And the step 
        #self.optim.step()

        #print('loss_mse : ', output_mse)
        return batch_loss, batch_kl, batch_ce

    def predict(self, batch, debug=False, custom_vect_input=None):
        lambs, poss, texts, labels, lens, _, lemmas = batch[:7]

        # Adjacency in the first matrix are identity matrices:
        #eyes = make_eyes(lambs, lens)

        # Set on cuda
        if self.cuda:
            lambs = lambs.cuda()
            texts = texts.cuda()
            labels = labels.cuda()
            #eyes = eyes.cuda()
            poss = poss.cuda()
            lemmas = lemmas.cuda()
        if custom_vect_input is None:
            # Embedding layers
            const_word_vec = self.embedding(texts)
            word_vec = self.word_embedding(texts)
            pos_vec = self.pos_embedding(poss)
            lemma_vec = self.lemma_embedding(lemmas)    
            
            x = torch.cat([word_vec, pos_vec, const_word_vec, lemma_vec], dim=2)
        else:
            x = custom_vect_input
        loss = []
        
        for sample in range(len(x)):
            lab_idx = 0
            for idx,val in enumerate(texts[sample]):
                if val == 2:
                    lab_idx = idx
        
            A_pred = self.model(x[sample],lambs[sample])
            
            
            loss_ce =  F.nll_loss(A_pred[lab_idx],labels[sample][lab_idx])
            loss.append(float(loss_ce.detach()))
        # first layer:
        # Adjacency matrix is the identity matrix.
        #x = self.first_layer(x, eyes)

        # MPNN model
        #x = self.mp_model(x, lambs)

        # last layer:
        #x = self.last_layer(x, eyes)

        # Mean pooling: We expect xTs is of shape (batch_size, seq_len, hidden_dim)
        #x = x.sum(1) / x.shape[1]

        # Propagate through the last layer:
        #logits = self.output_layer(x)

        return loss_ce
    
        
        
    
    def load(self, filename, cuda=False):
        if cuda:
            device = torch.device('cuda')
        else:
            device = torch.device('cpu')
        try:
            checkpoint = torch.load(filename + 'model_params.pt', map_location=device)
        except BaseException:
            print("Cannot load model from {}".format(filename + 'model_params.pt'))
            exit()

        self.embedding.load_state_dict(checkpoint['embedding'])
        self.pos_embedding.load_state_dict(checkpoint['pos_embedding'])
        self.word_embedding.load_state_dict(checkpoint['word_embedding'])
        self.lemma_embedding.load_state_dict(checkpoint['lemma_embedding'])
        self.model.load_state_dict(checkpoint['mp_model'])
        #self.output_layer.load_state_dict(checkpoint['output_layer'])
        #self.last_layer.load_state_dict(checkpoint['last_layer'])
        #self.first_layer.load_state_dict(checkpoint['first_layer'])

        self.vocab.load(filename + 'vocab.p')
        self.pos_vocab.load(filename + 'pos_vocab.p')
        self.lemma_vocab.load(filename + 'lemma_vocab.p')

        self.vocab.word_embed = self.embedding
        self.pos_vocab.word_embed = self.pos_embedding

    def save(self, filename):
        params = {
            'embedding': self.embedding.state_dict(),
            'pos_embedding': self.pos_embedding.state_dict(),
            'mp_model': self.model.state_dict(),
            #'output_layer': self.output_layer.state_dict(),
            #'last_layer': self.last_layer.state_dict(),
            #'first_layer': self.first_layer.state_dict(),
            'word_embedding': self.word_embedding.state_dict(),
            'lemma_embedding': self.lemma_embedding.state_dict()
        }
        try:
            torch.save(params, filename + 'model_params.pt')
            self.vocab.save(filename + 'vocab.p')
            self.pos_vocab.save(filename + 'pos_vocab.p')
            self.lemma_vocab.save(filename + 'lemma_vocab.p')

        except BaseException:
            print("[Warning: Saving failed... continuing anyway.]")


In [55]:
mp_trainer.optim.param_groups


[{'params': [Parameter containing:
   tensor([[-0.0273,  0.0097, -0.0463,  ...,  0.0418, -0.0671, -0.0421],
           [ 0.0486, -0.0559,  0.0185,  ...,  0.0292,  0.0125,  0.0012],
           [-0.0021, -0.0091, -0.0244,  ..., -0.0537,  0.0506,  0.0640],
           ...,
           [-0.0766,  0.0362, -0.0041,  ...,  0.0281, -0.0720,  0.0202],
           [ 0.0331,  0.0443, -0.0049,  ..., -0.0254, -0.0323, -0.0104],
           [-0.0283, -0.0145,  0.0110,  ..., -0.0656, -0.0682, -0.0232]],
          device='cuda:0', requires_grad=True),
   Parameter containing:
   tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
           1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
           1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
           1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
           1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
           1., 1., 1.,

In [54]:
mp_trainer = MLM(cfg, cuda=cfg['cuda'])

In [56]:
epochs = 3

for epoch in tqdm(range(epochs + 1)):

    if epoch > 0:
        for g in mp_trainer.optim.param_groups:
            g['lr'] = g['lr']/2

    for g in mp_trainer.optim.param_groups:
            print(g['lr'])
    if epoch == range(epochs):
        # It's the last epoch, don't train again.
        break

    print('Train epoch {}:'.format(epoch))
    epoch_loss = []
    kl_loss = []
    ce_loss = []
    for i, batch in enumerate(train_loader):
        loss,kl,ce = mp_trainer.update(batch)
        #break
        epoch_loss += loss
        kl_loss += kl
        ce_loss += ce
        if i % 25 == 0:
            print('step : ', i)
            print('avg_loss = ',sum(epoch_loss) / len(epoch_loss))
            print('avg_kl = ',sum(kl_loss) / len(kl_loss))
            print('avg_ce = ',sum(ce_loss) / len(ce_loss))
    mp_trainer.save('model/epoch_'+ str(epoch) +'_' + str(sum(epoch_loss) / len(epoch_loss)) + '__')
    #performance['loss'].append(np.mean(np.array(epoch_loss)))

  0%|                                                                                            | 0/4 [00:00<?, ?it/s]

1e-05
Train epoch 0:
step :  0
avg_loss =  23.021027266979218
avg_kl =  -13.442246913909912
avg_ce =  9.578780591487885
step :  25
avg_loss =  10.452911294137056
avg_kl =  -1.7338587601597493
avg_ce =  8.719052547230744
step :  50
avg_loss =  9.380426922575662
avg_kl =  -1.023954890814482
avg_ce =  8.356472040051777
step :  75
avg_loss =  8.842272822781908
avg_kl =  -0.7725851080919567
avg_ce =  8.069687723071853
step :  100
avg_loss =  8.512031941803745
avg_kl =  -0.6454635581720879
avg_ce =  7.866568388352816
step :  125
avg_loss =  8.28268463812798
avg_kl =  -0.5382260237450874
avg_ce =  7.744458618773414
step :  150
avg_loss =  8.162556788742247
avg_kl =  -0.4648045614756496
avg_ce =  7.697752231435961
step :  175
avg_loss =  8.049624396403404
avg_kl =  -0.4067476153881712
avg_ce =  7.642876784952188
step :  200
avg_loss =  7.946524364642094
avg_kl =  -0.36644722464777046
avg_ce =  7.580077143302605
step :  225
avg_loss =  7.831593128716556
avg_kl =  -0.32909610643323545
avg_ce =  

step :  2025
avg_loss =  7.111439560354564
avg_kl =  -0.047319328736032104
avg_ce =  7.064120231373918
step :  2050
avg_loss =  7.106577503977237
avg_kl =  -0.046758356775229354
avg_ce =  7.059819146973104
step :  2075
avg_loss =  7.107188938337287
avg_kl =  -0.046210724831718474
avg_ce =  7.060978213397855
step :  2100
avg_loss =  7.105439932778717
avg_kl =  -0.04568750762435182
avg_ce =  7.059752424987648
step :  2125
avg_loss =  7.1030699607912275
avg_kl =  -0.04576480664358398
avg_ce =  7.057305153954851
step :  2150
avg_loss =  7.099530628025577
avg_kl =  -0.04528888417923107
avg_ce =  7.054241743530665
step :  2175
avg_loss =  7.098616351314615
avg_kl =  -0.04478089107108056
avg_ce =  7.053835459838178
step :  2200
avg_loss =  7.097956567688914
avg_kl =  -0.044314541449023075
avg_ce =  7.053642025840831
step :  2225
avg_loss =  7.095858633219179
avg_kl =  -0.0438316949808038
avg_ce =  7.052026937875594
step :  2250
avg_loss =  7.095719160636935
avg_kl =  -0.04335197251784913
avg_

step :  4025
avg_loss =  7.007284785664474
avg_kl =  -0.02446913381254738
avg_ce =  6.982815651397801
step :  4050
avg_loss =  7.006761764172397
avg_kl =  -0.024318346764291843
avg_ce =  6.982443417051961
step :  4075
avg_loss =  7.005762664202865
avg_kl =  -0.024169401998217634
avg_ce =  6.981593261813672
step :  4100
avg_loss =  7.003419649556262
avg_kl =  -0.024022278992036326
avg_ce =  6.979397370219236
step :  4125
avg_loss =  7.000710455837147
avg_kl =  -0.0238769158050129
avg_ce =  6.976833539662149
step :  4150
avg_loss =  6.999918462864797
avg_kl =  -0.023733308414947238
avg_ce =  6.9761851540506825
step :  4175
avg_loss =  6.999047410726797
avg_kl =  -0.023591463356385886
avg_ce =  6.975455946931259
step :  4200
avg_loss =  6.997897623952249
avg_kl =  -0.023451319936697496
avg_ce =  6.9744463035603905
step :  4225
avg_loss =  6.997883310894772
avg_kl =  -0.023312818482024548
avg_ce =  6.974570491896811
step :  4250
avg_loss =  6.996398062411479
avg_kl =  -0.02317590651307645


 25%|██████████████████▊                                                        | 1/4 [11:10:47<33:32:23, 40247.77s/it]

...

1.25e-06
Train epoch 3:
step :  0
avg_loss =  5.845082566142082
avg_kl =  -4.336237907409668e-06
avg_ce =  5.845078211277723
step :  25
avg_loss =  6.528014274788662
avg_kl =  -3.244727849960327e-06
avg_ce =  6.528011029917532
step :  50
avg_loss =  6.739778364447
avg_kl =  -3.5977173669665467e-06
avg_ce =  6.739774765159168
step :  75
avg_loss =  6.732341171441428
avg_kl =  -3.3662164289700356e-06
avg_ce =  6.732337803215303
step :  100
avg_loss =  6.742765801112135
avg_kl =  -3.5376795152626416e-06
avg_ce =  6.742762259504468
step :  125
avg_loss =  6.747505502484735
avg_kl =  -3.4992006563004995e-06
avg_ce =  6.747502001983184
step :  150
avg_loss =  6.786653524702214
avg_kl =  -3.4610784014329216e-06
avg_ce =  6.786650063364769
step :  175
avg_loss =  6.7930892531480405
avg_kl =  -3.424843519248746e-06
avg_ce =  6.7930858280293585
step :  200
avg_loss =  6.7864270988782
avg_kl =  -3.390310712121612e-06
avg_ce =  6.78642370727939
step :  225
avg_loss =  6.764172671587476
avg_kl =  -

step :  1975
avg_loss =  6.742537700817644
avg_kl =  -3.2677441488514063e-06
avg_ce =  6.742534433216776
step :  2000
avg_loss =  6.745544136777873
avg_kl =  -3.2659309140328823e-06
avg_ce =  6.745540871008928
step :  2025
avg_loss =  6.745293842371142
avg_kl =  -3.2704656342410384e-06
avg_ce =  6.745290572012155
step :  2050
avg_loss =  6.744615076873026
avg_kl =  -3.263991832849399e-06
avg_ce =  6.744611812955663
step :  2075
avg_loss =  6.7446465032851615
avg_kl =  -3.2550136707651363e-06
avg_ce =  6.744643248441964
step :  2100
avg_loss =  6.741842587504616
avg_kl =  -3.2497838543801576e-06
avg_ce =  6.741839337934421
step :  2125
avg_loss =  6.740082475647772
avg_kl =  -3.2434706082909262e-06
avg_ce =  6.740079232417222
step :  2150
avg_loss =  6.738647052790039
avg_kl =  -3.2386454605934287e-06
avg_ce =  6.738643814348076
step :  2175
avg_loss =  6.73739111683742
avg_kl =  -3.245004336349666e-06
avg_ce =  6.737387872036811
step :  2200
avg_loss =  6.738031792507582
avg_kl =  -3.2

step :  3950
avg_loss =  6.747572157901134
avg_kl =  -3.0722971642599685e-06
avg_ce =  6.747569085590298
step :  3975
avg_loss =  6.747027651472648
avg_kl =  -3.0742620888130526e-06
avg_ce =  6.747024577142631
step :  4000
avg_loss =  6.746690186145705
avg_kl =  -3.07131330539691e-06
avg_ce =  6.7466871147127545
step :  4025
avg_loss =  6.749181453424699
avg_kl =  -3.0683770857222094e-06
avg_ce =  6.749178384887998
step :  4050
avg_loss =  6.7502974855040785
avg_kl =  -3.0666270636535228e-06
avg_ce =  6.7502944186926355
step :  4075
avg_loss =  6.751386690070522
avg_kl =  -3.0644474710110243e-06
avg_ce =  6.751383625366686
step :  4100
avg_loss =  6.752661576370226
avg_kl =  -3.0642815462934247e-06
avg_ce =  6.752658511825247
step :  4125
avg_loss =  6.752685298494913
avg_kl =  -3.0616766913562393e-06
avg_ce =  6.7526822365767005
step :  4150
avg_loss =  6.753078066775087
avg_kl =  -3.0637596011650013e-06
avg_ce =  6.753075002797855
step :  4175
avg_loss =  6.754216007393542
avg_kl =  

step :  5925
avg_loss =  6.761666286199323
avg_kl =  -3.0349926231601856e-06
avg_ce =  6.761663251403148
step :  5950
avg_loss =  6.761185985405171
avg_kl =  -3.03257191016922e-06
avg_ce =  6.761182953022937


100%|██████████████████████████████████████████████████████████████████████████████| 4/4 [44:59:14<00:00, 40488.54s/it]


In [92]:
torch.cuda.empty_cache()

In [81]:
len(epoch_loss)

190880

In [114]:
torch.exp(torch.as_tensor(5.08551229556906))

tensor(161.6627)

In [77]:
per = []
for i in range(len(epoch_loss)): 
    print(torch.exp(torch.as_tensor((epoch_loss[i]))),epoch_loss[i])

tensor(203.2776) 5.314572334289551
tensor(527.9638) 6.2690277099609375
tensor(673.9417) 6.513143539428711
tensor(9.7217) 2.274357557296753
tensor(1445.9209) 7.276501655578613
tensor(32.8890) 3.493138074874878
tensor(3.8168) 1.339421033859253
tensor(11555.5859) 9.354924201965332
tensor(160741.0156) 11.987549781799316
tensor(88.4741) 4.482709884643555
tensor(85673.0469) 11.358293533325195
tensor(1903.1265) 7.551253318786621
tensor(1551.2001) 7.3467841148376465
tensor(60.1737) 4.097234725952148
tensor(20505.8379) 9.928464889526367
tensor(294.1004) 5.6839213371276855
tensor(142.6219) 4.9601969718933105
tensor(939.1973) 6.845025539398193
tensor(18.5275) 2.9192538261413574
tensor(15.4807) 2.7395970821380615
tensor(3765.2234) 8.233562469482422
tensor(217.2650) 5.381117820739746
tensor(139413.6250) 11.845200538635254
tensor(14874.1338) 9.607378959655762
tensor(16.7678) 2.8194587230682373
tensor(59.1039) 4.0792975425720215
tensor(3.9777) 1.3807153701782227
tensor(3.3631) 1.212864637374878
tenso

tensor(209.4375) 5.344425201416016
tensor(15.7882) 2.759260654449463
tensor(4126.3936) 8.325159072875977
tensor(13.4008) 2.595310688018799
tensor(1265.0762) 7.142887592315674
tensor(22.2607) 3.102822780609131
tensor(252.5871) 5.5317559242248535
tensor(756949.7500) 13.537052154541016
tensor(114.4971) 4.740549564361572
tensor(18779.4590) 9.840518951416016
tensor(1044.3689) 6.951168060302734
tensor(8.2079) 2.1050984859466553
tensor(159356.1719) 11.978897094726562
tensor(1.1148) 0.10866787284612656
tensor(70096.5625) 11.157629013061523
tensor(211320.1094) 12.261129379272461
tensor(411.5421) 6.019911289215088
tensor(26039.8711) 10.167384147644043
tensor(462.3453) 6.136312007904053
tensor(20478.7129) 9.927141189575195
tensor(157.6967) 5.060673236846924
tensor(13114.6768) 9.481487274169922
tensor(1951.3622) 7.576282978057861
tensor(8026.6948) 8.990528106689453
tensor(37.9594) 3.63651704788208
tensor(1802.8735) 7.497137069702148
tensor(359.1386) 5.883708477020264
tensor(196.2131) 5.27920150756

tensor(126988.8906) 11.75185489654541
tensor(2491.5376) 7.820655345916748
tensor(51500.9570) 10.849355697631836
tensor(368.7527) 5.910126209259033
tensor(523.4252) 6.260394096374512
tensor(18841.8691) 9.843836784362793
tensor(16.4031) 2.7974724769592285
tensor(149.7885) 5.0092244148254395
tensor(12150.8945) 9.405158042907715
tensor(15256.4717) 9.632759094238281
tensor(1454.1288) 7.282162189483643
tensor(2113.0156) 7.655871391296387
tensor(1819.9315) 7.506554126739502
tensor(15430.6729) 9.644112586975098
tensor(109.8440) 4.699060916900635
tensor(40.3371) 3.6972708702087402
tensor(11.9085) 2.477252960205078
tensor(34.3280) 3.5359625816345215
tensor(13.7353) 2.6199686527252197
tensor(2.0162) 0.7012139558792114
tensor(293.1485) 5.6806793212890625
tensor(4420.4854) 8.394004821777344
tensor(2090.3909) 7.645106315612793
tensor(4.7694) 1.5622225999832153
tensor(5835.2080) 8.67166519165039
tensor(230725.0156) 12.348981857299805
tensor(4.3765) 1.4762396812438965
tensor(9.2619) 2.225904941558838


tensor(1.2469) 0.2206268608570099
tensor(9.7600) 2.278296947479248
tensor(208093.1094) 12.24574089050293
tensor(30.4923) 3.4174740314483643
tensor(67.0686) 4.205715656280518
tensor(25660.5234) 10.152709007263184
tensor(991.5455) 6.899264812469482
tensor(18.4840) 2.9169044494628906
tensor(29591.1016) 10.295228958129883
tensor(660.2941) 6.492685317993164
tensor(3.6057) 1.2825126647949219
tensor(30686.4746) 10.33157730102539
tensor(465.5069) 6.143126964569092
tensor(15490.2402) 9.647965431213379
tensor(22598.3438) 10.02563190460205
tensor(26670.6367) 10.19131851196289
tensor(850.2445) 6.745523929595947
tensor(193.3664) 5.264586925506592
tensor(368.6447) 5.9098334312438965
tensor(17455.6543) 9.76741886138916
tensor(407.2154) 6.009342193603516
tensor(24575.3926) 10.109500885009766
tensor(934.3801) 6.839883327484131
tensor(3398.2593) 8.13101863861084
tensor(886.5016) 6.787282943725586
tensor(3987.2776) 8.290863990783691
tensor(2.4896) 0.9121328592300415
tensor(4.9438) 1.5981347560882568
tens

tensor(15276.1992) 9.634051322937012
tensor(69235.0625) 11.145262718200684
tensor(9995.4248) 9.209882736206055
tensor(107.6497) 4.678882598876953
tensor(1261.0536) 7.139702796936035
tensor(15383.7129) 9.641064643859863
tensor(269.2017) 5.595460891723633
tensor(7146.6924) 8.874404907226562
tensor(593.1826) 6.385502338409424
tensor(50.2689) 3.9173872470855713
tensor(258.7198) 5.555745601654053
tensor(4996.7998) 8.516552925109863
tensor(74.5053) 4.3108696937561035
tensor(165.5031) 5.10899019241333
tensor(1291.6765) 7.1636962890625
tensor(88.5763) 4.483864784240723
tensor(735.0920) 6.5999956130981445
tensor(18.1055) 2.8962149620056152
tensor(174.9216) 5.164338111877441
tensor(610.1256) 6.413664817810059
tensor(12.3317) 2.512174129486084
tensor(68809.3750) 11.139095306396484
tensor(173.9363) 5.158689022064209
tensor(10150.3799) 9.225266456604004
tensor(690.3914) 6.537258625030518
tensor(430.3458) 6.064589023590088
tensor(34349.7578) 10.444350242614746
tensor(92.1906) 4.523858070373535
tenso

...

tensor(3346.5859) 8.11569595336914
tensor(22.3554) 3.107067823410034
tensor(698.6931) 6.549211502075195
tensor(991.4287) 6.899147033691406
tensor(450.5793) 6.110534191131592
tensor(4.4483) 1.4925326108932495
tensor(14818.7451) 9.60364818572998
tensor(3349.5010) 8.11656665802002
tensor(16103.2002) 9.686773300170898
tensor(72053.1797) 11.185159683227539
tensor(27.8454) 3.326667070388794
tensor(188.4654) 5.238914489746094
tensor(97438.2188) 11.486973762512207
tensor(144.5976) 4.973954677581787
tensor(38.4023) 3.648116111755371
tensor(230.8091) 5.441590785980225
tensor(13029.7920) 9.474993705749512
tensor(3.4603) 1.2413619756698608
tensor(1573.7386) 7.361209392547607
tensor(188.0214) 5.236555576324463
tensor(169.0228) 5.130033493041992
tensor(5.0418) 1.6177657842636108
tensor(556368.5000) 13.229186058044434
tensor(133429.7656) 11.80133056640625
tensor(13314.6621) 9.496621131896973
tensor(41251.9570) 10.627453804016113
tensor(1326.8041) 7.190528392791748
tensor(1041.9564) 6.948855400085449


tensor(2284.6013) 7.733946800231934
tensor(1.6211) 0.48312291502952576
tensor(23330.3945) 10.057512283325195
tensor(22460.8555) 10.019529342651367
tensor(747.8121) 6.617151737213135
tensor(3536.5503) 8.170907020568848
tensor(19278.2461) 9.866732597351074
tensor(1137.8065) 7.036857604980469
tensor(175.4872) 5.167566299438477
tensor(1201.6102) 7.0914177894592285
tensor(431.3957) 6.067025661468506
tensor(193.7490) 5.266563415527344
tensor(46.7768) 3.845386505126953
tensor(80.7772) 4.39169454574585
tensor(26633.7051) 10.189932823181152
tensor(2.3489) 0.8539400100708008
tensor(139.9458) 4.941255569458008
tensor(7.0461) 1.952469825744629
tensor(57169.6953) 10.953779220581055
tensor(75152.0859) 11.227269172668457
tensor(11903.2451) 9.384566307067871
tensor(14.5027) 2.6743381023406982
tensor(1.0528) 0.051478274166584015
tensor(10960.2627) 9.302031517028809
tensor(591.6603) 6.382932662963867
tensor(188.1965) 5.237486839294434
tensor(15145.6875) 9.625471115112305
tensor(647.9111) 6.4737534523010

tensor(1057.7035) 6.963855266571045
tensor(91.8881) 4.520571708679199
tensor(1257.0120) 7.136492729187012
tensor(22.7657) 3.1252529621124268
tensor(1332.8256) 7.195056438446045
tensor(1827.0676) 7.510467529296875
tensor(2174.9917) 7.684780120849609
tensor(47142.4492) 10.760929107666016
tensor(5475.4790) 8.60803508758545
tensor(41.6358) 3.7289607524871826
tensor(14551.3174) 9.585436820983887
tensor(1472.9767) 7.295040607452393
tensor(12087.4189) 9.399920463562012
tensor(28.8404) 3.3617782592773438
tensor(657.1875) 6.487969398498535
tensor(16355.8213) 9.702339172363281
tensor(118918.9297) 11.686197280883789
tensor(342.6359) 5.836668491363525
tensor(56721.0117) 10.945899963378906
tensor(449.6328) 6.108431339263916
tensor(726.9357) 6.58883810043335
tensor(42.3813) 3.7467076778411865
tensor(13281.0938) 9.494096755981445
tensor(2832.6770) 7.948977470397949
tensor(47.6794) 3.864500045776367
tensor(15858.4883) 9.671460151672363
tensor(25.3234) 3.231727123260498
tensor(177.8115) 5.1807241439819

tensor(78.1561) 4.358707904815674
tensor(2.3192) 0.8412364721298218
tensor(2082.0227) 7.641095161437988
tensor(172.0755) 5.147933483123779
tensor(25.8138) 3.250910997390747
tensor(24.1117) 3.1826958656311035
tensor(31620.6484) 10.361565589904785
tensor(2560.1028) 7.847802639007568
tensor(311.3561) 5.740937232971191
tensor(13642.2188) 9.52092456817627
tensor(24268.6816) 10.096941947937012
tensor(719.6667) 6.5787882804870605
tensor(61.0358) 4.111461162567139
tensor(149253.3750) 11.913400650024414
tensor(413.6314) 6.024975299835205
tensor(273.9973) 5.6131181716918945
tensor(177.6007) 5.179537773132324
tensor(14918.0869) 9.610329627990723
tensor(64228.3477) 11.070199966430664
tensor(18468.3613) 9.823814392089844
tensor(28694.6582) 10.264466285705566
tensor(428.9663) 6.061378479003906
tensor(352.7731) 5.865825176239014
tensor(2831.5291) 7.948572158813477
tensor(2653.2463) 7.883539199829102
tensor(11643.5293) 9.362505912780762
tensor(714.9845) 6.572260856628418
tensor(347.0023) 5.84933137893

tensor(159.4102) 5.071480751037598
tensor(1161.3521) 7.057340145111084
tensor(27153.2324) 10.209251403808594
tensor(278.6939) 5.6301140785217285
tensor(299.2208) 5.701181888580322
tensor(26.1391) 3.2634308338165283
tensor(14250.0010) 9.564512252807617
tensor(6.9056) 1.932338833808899
tensor(534.5287) 6.28138542175293
tensor(47.4279) 3.859210968017578
tensor(38028.7500) 10.546097755432129
tensor(177.3784) 5.178285598754883
tensor(19126.3984) 9.858824729919434
tensor(24.0990) 3.1821701526641846
tensor(67.2319) 4.208148002624512
tensor(138.5086) 4.930932521820068
tensor(141.5521) 4.952667713165283
tensor(448052.5312) 13.012665748596191
tensor(48.4877) 3.881310224533081
tensor(67602.2188) 11.1213960647583
tensor(1130.8643) 7.030737400054932
tensor(88.0599) 4.4780168533325195
tensor(185.8095) 5.224721908569336
tensor(88239.2266) 11.38780689239502
tensor(20217.7695) 9.91431713104248
tensor(262.0811) 5.5686540603637695
tensor(72764.3594) 11.194981575012207
tensor(163.3495) 5.095891952514648
t

In [290]:
lo = MLM(cfg, cuda=cfg['cuda'])


In [291]:
lo.load('model\epoch_3_6.761289965409006__',True)

In [136]:
lo

In [160]:
total_loss = []
for i, batch in enumerate(test_loader):
    total_loss.append(lo.predict(batch))
    

KeyboardInterrupt: 

In [110]:
l = []
for i in total_loss: 
    l.append(sum(i)/32)

In [39]:
#from matplotlib import pyplot as plt
#plt.plot(range(len(l)),l)
#plt.xlabel("batch")
#plt.ylabel("reconstruction loss")
#plt.show()

In [143]:
import captum
from captum.attr import IntegratedGradients, Occlusion, LayerGradCam, LayerAttribution
from captum.attr import visualization as viz

In [38]:
lo = MLM(cfg, cuda=cfg['cuda'])
lo.load('model\epoch_3_6.761289965409006__',True)


In [39]:
test_loader = DataLoader(test_data,
                         batch_size=1,
                         collate_fn=collate_fn,
                        drop_last=True)

In [40]:
from matplotlib import pyplot as plt

## viz

In [41]:
import torch
import numpy as np
import copy
import torch.nn as nn
import networkx as nx

#from networkx.drawing.nx_pydot import graphviz_layout
#import matplotlib.pyplot as plt
from torch import optim

from torch.autograd import Variable


class Gnnexplainer():
    def __init__(self, lr, momentum, epochs, model, init_val = 0.0):
        self.lr = lr
        self.momentum = momentum
        self.epochs = epochs
        self.model = model
        self.init_val = init_val

    def explain(self, batch, output_id=None, graph_part='edges'):
        # unwrap batch
        #if self.model.new_model:
        adjs, poss, texts, labels, lens, root_ids, lemmas = batch[:7]
        adjs = adjs[0].unsqueeze(0).cuda()
        poss = poss[0].unsqueeze(0).cuda()
        texts = texts[0].unsqueeze(0).cuda()
        labels = labels[0].unsqueeze(0).cuda()
        #lens = lens[0].unsqueeze(0)
        root_ids = root_ids[0].unsqueeze(0).cuda()
        lemmas = lemmas[0].unsqueeze(0).cuda()
        
        #else:
        #    adjs, poss, texts, labels, lens, root_ids = batch
        assert adjs.shape[0] == 1, 'Please one sample at a time'
        
        if graph_part == 'edges':
            Z = Variable(torch.ones(adjs.shape) * self.init_val, requires_grad=True)  # Just init with ones for now.

            optimizer = optim.SGD([Z], lr=self.lr, momentum=self.momentum)

            # get the output label:
            #if output_id is None:
            #    output_id = self.model.predict(batch).argmax(dim=1)[0]

            # Do the masking.
            adjs_masked = adjs * torch.sigmoid(Z.cuda())
            if self.model.new_model:
                batch_masked = adjs_masked, poss, texts, labels, lens, root_ids, lemmas
            else:
                batch_masked = adjs_masked, poss, texts, labels, lens, root_ids

            x = None # Just a placeholder
            
        elif graph_part == 'nodes':
            # Prepare custom vectorial text input:
            # Embedding layers
            const_word_vec = self.model.embedding(texts)
            word_vec = self.model.word_embedding(texts)
            pos_vec = self.model.pos_embedding(poss)
            lemma_vec = self.model.lemma_embedding(lemmas)
            x = torch.cat([word_vec, pos_vec, const_word_vec, lemma_vec], dim=2)
            
            # Generate trainable matrix:
            Z = Variable(torch.zeros(x.shape), requires_grad=True)
            optimizer = optim.Adam([Z], lr=self.lr)
            batch_masked = batch # just a placeholder
        else:
            raise NotImplementedError

        # start training
        losses = []
        time_error_func = torch.nn.MSELoss()
        
        for epoch in range(self.epochs):
            # Push through the network.
            optimizer.zero_grad()
            out_y = self.model.predict(batch_masked, custom_vect_input=x)
            #print(out_y)
            out_y.backward(retain_graph=True)
            optimizer.step()
            #print(optimizer.param_groups)
            losses.append(time_error_func(torch.sigmoid(torch.zeros(Z.shape)), torch.sigmoid(Z)))

        if graph_part == 'edges':
            relevances = {}
            for non_zero in adjs.nonzero():
                relevance_score = Z[non_zero[0], non_zero[1], non_zero[2]].data
                relevances[(int(non_zero[1]), int(non_zero[2]))] = relevance_score

        elif graph_part == 'nodes':
            relevances = Z[0].data

        else:
            raise NotImplementedError

        return relevances, losses


In [42]:
gnnexpl = Gnnexplainer(lr=0.01,
                       momentum=0.9,
                       epochs=20,
                       model=lo,
                       init_val=0.1)

In [43]:
test_batches_list = list(test_loader)

In [44]:
test_set = test_data.sst_data

In [1]:
len(test_batches_list)

NameError: name 'test_batches_list' is not defined

In [49]:
for new_id, sample_id in enumerate(test_batches_list):
    sample = test_batches_list[new_id]
    adjs, poss, texts, labels, lens, root_ids = sample[:6]
    
    real_text = ' '.join(vocab.unmap(labels[0].tolist()))
    real_text = real_text.replace('<','')
    real_text = real_text.replace('>','')
    real_text = nlp(real_text)
    lab_idx = 0
    for idx,val in enumerate(texts[0]):
        if val == 2:
            lab_idx = idx
            
    #print(vocab.unmap([labels[0][lab_idx].item()]))
    relevances, loss = gnnexpl.explain(sample,graph_part='edges')
    relevances = list(relevances.items())
    #prediction = mp_trainer.predict(sample).argmax(dim=1)
    draw_walks = True
    #print(real_text)
    fig = plt.figure(figsize=(75,75))
    ax = plt.subplot()
    ax = plot_relevance(sample,
                           relevances,
                           real_text,
                           ax=ax,
                           draw_walks=True
                           )
    ax.axis('off')
    plt.tight_layout()
    label = vocab.unmap([labels[0][lab_idx].item()])[0]
    try:
        pic_file = 'vis/'+label+'_' + str(new_id) + '.png'
        print('save pic at {}'.format(pic_file))
        plt.savefig(pic_file, transparent=False)
    except:
        pass
    plt.close()

save pic at vis/<UNK>_0.png
save pic at vis/)_1.png
save pic at vis/was_2.png
save pic at vis/,_3.png
save pic at vis/initially_4.png
save pic at vis/poems_5.png
save pic at vis/called_6.png
save pic at vis/traditional_7.png
save pic at vis/since_8.png
save pic at vis/another_9.png
save pic at vis/the_10.png
save pic at vis/suggests_11.png
save pic at vis/=_12.png
save pic at vis/grandfather_13.png
save pic at vis/was_14.png
save pic at vis/later_15.png
save pic at vis/shortly_16.png
save pic at vis/an_17.png
save pic at vis/also_18.png
save pic at vis/of_19.png
save pic at vis/by_20.png
save pic at vis/the_21.png
save pic at vis/<UNK>_22.png
save pic at vis/<UNK>_23.png
save pic at vis/concludes_24.png
save pic at vis/he_25.png
save pic at vis/<UNK>_26.png
save pic at vis/he_27.png
save pic at vis/next_28.png
save pic at vis/,_29.png
save pic at vis/describes_30.png
save pic at vis/<UNK>_31.png
save pic at vis/<UNK>_32.png
save pic at vis/have_33.png
save pic at vis/<UNK>_34.png
save 


KeyboardInterrupt



In [46]:
def plot_relevance(sample,
                   relevances,
                   real_text,
                   circ_h=0.1,
                   circ_v=0.05,
                   ax=None,
                   filt_width=1.7,
                   font_size=40,
                   node_size=30,
                   walk_width=1,
                   convolve=True,
                   relevance_scaling=1.,
                   random_scal=0.14,
                   scale_by_sentlen=False,
                   scale_by_max=True,
                   graph_layout=False,  # False is circle layout
                   fract_of_circ=1 / 8,
                   draw_walks=True,  # False is draw edges
                   ):
    adjs, poss, texts, labels, lens, root_ids = sample[:6]
    adjs, poss, texts, labels, lens, root_ids, lemmas = batch[:7]
    adjs = adjs[0].unsqueeze(0)
    poss = poss[0].unsqueeze(0)
    texts = texts[0].unsqueeze(0)
    labels = labels[0].unsqueeze(0)
    #lens = lens[0].unsqueeze(0)
    root_ids = root_ids[0].unsqueeze(0)
    lemmas = lemmas[0].unsqueeze(0)

    assert adjs.shape[0] == 1, 'One sample at at time please.'
    nodes = [token.i for token in real_text]
    #print(list(zip(np.array(adjs[0]).nonzero()[0], np.array(adjs[0]).nonzero()[1])))
    if ax is None:
        fig = plt.figure(figsize=(10, 10))
        ax = plt.subplot(1, 1, 1)

    if graph_layout:
        edges = []
        for token in real_text:
            if token.dep_ == 'ROOT':
                continue
            edges.append([token.head.i, token.i])
            
        print(edges)
        # Check if the edges coincide with the input connections
        #print(np.shape(edges),np.shape(adjs.nonzero()))
        assert np.array(
            [tuple(edge) in list(zip(np.array(adjs[0]).nonzero()[0], np.array(adjs[0]).nonzero()[1])) for edge in
             edges]).all(), 'Edges doesnt coincide with the input adj, {}, {}'.format(edges, adjs.nonzero())

        G = nx.DiGraph()
        G.add_nodes_from(nodes)
        G.add_edges_from(edges)
        pos = graphviz_layout(G, prog='dot', root=int(root_ids[0]))

        pos = {i: np.array(p) for i, p in pos.items()} # Make the pos to arrays
        pos = {i: np.array(p) for i, p in pos.items()} # Make the pos to arrays
    else:

        edges = [list(edge.numpy()) for edge in adjs[0].nonzero()]
        num_words = len(real_text)
        neglect_circ = int(num_words * (fract_of_circ))

        G = nx.path_graph(num_words + int(neglect_circ))

        # Take the middle nodes in all nodes
        plot_nodes = [i for i in range(len(texts[0]))][::-1]

        pos = nx.circular_layout(G)
        pos = pos.copy()
        # make a shift
        for shift in range(int(len(pos) / 4 - neglect_circ / 8)):
            # Take last element:
            xl = pos[len(pos) - 1]
            # Shift every element but the last
            pos = {i + 1: pos[i] for i in range(len(pos) - 1)}
            pos[0] = xl
        # change order to coincide with the text
        pos = {len(pos) - i - 1: p for i, p in pos.items()}

    # make the positions fit optimally in a circle of radius \sqrt n in [0,0]:
    # compute mean:
    center = sum([p for _, p in pos.items()])
    pos = {i : p - center/len(pos) for i, p in pos.items()}
    maximum = max([p.max() for _, p in pos.items()])
    if True: # ball of radius sqrt n
        pos = {i : np.sqrt(lens[0])*p/maximum for i, p in pos.items()}
        circ_h *= np.sqrt(lens[0])
        circ_v *= np.sqrt(lens[0])
    else: # ball of radius 1
        pos = {i : p/maximum for i, p in pos.items()}

    #nx.draw_networkx_edges(G,
    #                       pos,
    #                       edgelist=edges,
    #                       alpha=1,
    #                       style='dotted',
    #                       ax=ax,
    #                       arrows=False)

    nx.draw_networkx_nodes(G,
                           pos,
                           nodelist=nodes,
                           node_color='w',
                           alpha=1,
                           node_size=node_size,
                           ax=ax,
                           linewidths=1,
                           node_shape='o',
                           # label=[label_char[curr_label]]
                           )

    node_chars = {token.i: token.text for token in real_text}

    text_items = nx.draw_networkx_labels(G,
                                         pos,
                                         labels=node_chars,
                                         font_size=font_size,
                                         font_color='k',
                                         font_family='sans-serif',
                                         font_weight='normal',
                                         alpha=1.0,
                                         ax=ax
                                         )

    if draw_walks:
        # Draw walks
        for walk, relevance in relevances:
            if scale_by_sentlen:
                color, alpha = make_relevance_color(relevance, relevance_scaling * len(nodes))
            elif scale_by_max:
                scal_param = max([abs(float(relev.sum())) for _, relev in relevances])
                color, alpha = make_relevance_color(relevance, relevance_scaling / scal_param)
            else:
                color, alpha = make_relevance_color(relevance, relevance_scaling)
            rx = [pos[node][0] for node in walk]
            ry = [pos[node][1] for node in walk]

            rx, ry, xloops, yloops = smooth(rx,
                                            ry,
                                            random_scal=random_scal,
                                            filt_width=filt_width,
                                            circ_h=circ_h,
                                            circ_v=circ_v,
                                            convolve=convolve)

            ax.plot(rx, ry, color=color, alpha=alpha, lw=walk_width)

            for xloop, yloop in zip(xloops, yloops):
                ax.plot(xloop, yloop, color=color, alpha=alpha, lw=walk_width)
    else:
        assert len(relevances.shape) == 2 and relevances.shape[0] == len(real_text)
        # draw nodes
        # compose the colors:
        for i, t in text_items.items():
            if scale_by_max:
                scal_param = max([abs(float(relevances[i].sum())) for i in range(relevances.shape[0])])
                color, alpha = make_relevance_color(relevances[i], relevance_scaling / scal_param)
            else:
                color, alpha = make_relevance_color(relevances[i], relevance_scaling)

            # Set background of the nodes:
            t.set_bbox(dict(facecolor=color, alpha=alpha, edgecolor='white'))

    return ax


In [47]:
def make_relevance_color(relevance, scaling_val):
    color = 'b' if relevance.sum() < 0 else 'r'
    # first some scaling
    relevance_val = abs(relevance.data.sum()) * float(scaling_val)
    # clip alpha
    if abs(relevance_val) > 1.:
        alpha = 1.
    else:
        alpha = abs(relevance_val)

    return color, float(alpha)


In [48]:
def smooth(rx,
           ry,
           random_scal=0.02,
           grid_number=200,
           circ_h=0.2,
           circ_v=0.1,
           filt_width=1.5,
           convolve=False):


    # put some random noise on the poits itself:
    rrx = [x + np.random.normal(0, random_scal) for x in rx]
    rry = [y + np.random.normal(0, random_scal) for y in ry]

    xlines = []
    ylines = []

    xloops = []
    yloops = []

    for i in range(len(rx) - 1):
        if rx[i] == rx[i + 1] and ry[i] == ry[i + 1]:
            # self loop
            t_range = np.linspace(-np.pi * 3/2, np.pi/2, grid_number + 2)
            radius_range = np.ones(grid_number + 2)
            rx_loop = circ_h * radius_range * np.cos(t_range) + rrx[i]
            ry_loop = circ_v * radius_range * np.sin(t_range) + rry[i]

            xloops.append(rx_loop)
            yloops.append(ry_loop)

        else:
            # Linear interpolation
            rx_line = np.linspace(rrx[i], rrx[i + 1], grid_number)
            ry_line = np.linspace(rry[i], rry[i + 1], grid_number)

            xlines.append(rx_line)
            ylines.append(ry_line)

    if len(xlines) > 1:
        rx = np.concatenate(xlines)
        ry = np.concatenate(ylines)

        # We convolve if the previous point wasn't a self loop, therefore an edge:
        if convolve:
            filter_span = np.linspace(-filt_width, filt_width, grid_number)
            filt = np.exp( - filter_span ** 2)
            filt = filt / filt.sum()

            # Add some more points at the ends to prevent loss of the corners
            rx = np.concatenate([np.array([rx[0]] * (grid_number)),
                                 rx,
                                 np.array([rx[-1]] * (grid_number))])

            ry = np.concatenate([np.array([ry[0]] * (grid_number)),
                                 ry,
                                 np.array([ry[-1]] * (grid_number))])

            rx = np.convolve(rx, filt, mode='valid')
            ry = np.convolve(ry, filt, mode='valid')

        rx += np.random.normal(0, random_scal)
        ry += np.random.normal(0, random_scal)

        # Small adjustment
        rx = 0.9 * rx + 0.1 * rx.mean(axis=0)
        rx = 0.9 * rx + 0.1 * rx.mean(axis=0)

    return rx , ry, xloops, yloops




In [226]:
def create_text_heat_map(text, heat,  scal_val=1., font_size=20, break_at=6, scale_by_max=True):
    assert len(text) == len(heat), 'Sorry, the text and heat values needs to have same length.'

    if scale_by_max:
        scal_val /= max([abs(float(heat[i].sum())) for i in range(heat.shape[0])])
    
    # Adjust the heat:
    heat = [scal_val*h for h in heat]
        
    # clipping
    heat = [-1. if h< -1. else h for h in heat]
    heat = [1. if h > 1. else h for h in heat ]

    output = '<p><center>'

    for i in range(len(text)):

        if text[i].text not in [',', '.', ';', ':', "n't", "'s"]:
            output += ' '
        if text[i].text in ["n't"]:
            output +=  '<span style="font-size:30%;">&nbsp;</span>' # small space
        if heat[i] <= 0:
            output += '<text style="background-color:rgba(0, 0, 255,{});font-weight: bold; font-size:{}px;font-family: sans-serif;">{}</text>'.format(
                -heat[i],
                font_size,
                text[i]
            )
        else:
            output += '<text style="background-color:rgba(255, 0, 0,{});font-weight: bold;font-size:{}px;font-family: sans-serif;">{}</text>'.format(
                heat[i],
                font_size,
                text[i]
            )
        
        if i % break_at == 0 and i != 0:
            output+='<br>'
    
    output += '</center></p>'
    
    return output


In [227]:
html_string = create_text_heat_map(real_text, 
                                       relevances, 
                                       break_at=6)


AssertionError: Sorry, the text and heat values needs to have same length.

In [228]:
len(relevances)

450

## Train

In [32]:
def test_performance(data_loader, mp_trainer, num_of_classes = 64):
    # Evaluation
    f1_micro = 0
    prec_micro = 0
    recall_micro = 0
    accuracy = 0.
    for batch in data_loader:
        lambs, poss, texts, labels, lens = batch[:5]
        logits = mp_trainer.predict(batch)

        predicted_classes = torch.argmax(logits, dim=1)
        if num_of_classes == 2:
            average = 'binary'
        else:
            average = 'micro'
        f1_micro += f1_score(labels.cpu(), predicted_classes.cpu(), average= average)
        prec_micro += precision_score(labels.cpu(), predicted_classes.cpu(), average= average)
        recall_micro += recall_score(labels.cpu(), predicted_classes.cpu(), average= average)
        accuracy += accuracy_score(labels.cpu(), predicted_classes.cpu())

    f1_micro /= len(data_loader)
    prec_micro /= len(data_loader)
    recall_micro /= len(data_loader)
    accuracy /= len(data_loader)

    return f1_micro, prec_micro, recall_micro, accuracy


In [33]:
repo_name = 'saved_models/sst_model1+/'
cfg['trainerfilename'] = repo_name
cfg['logfilename'] = repo_name + 'log.txt'

# Task specific settings
cfg['num_of_classes'] = 64
cfg['language'] = 'en'

# model specific settings
cfg['normalize_lamb'] = True
cfg['laplacian'] = False


In [34]:
with open(cfg['logfilename'], 'a+') as logfile:
    logfile.write(
        '{} training samples set into {} batches, {} test samples set into {} batches\n'.format(len(train_data),
                                                                                                len(train_loader),
                                                                                                len(test_data),
                                                                                                len(test_loader)))
    logfile.write('Start training.\n')

all_losses = []
performance = {'acc_test': [], 'prec_test': [], 'f1_test': [], 'recall_test': [],
               'acc_train': [], 'prec_train': [], 'f1_train': [], 'recall_train': [],
               'loss': []}
print('Start training')
best_accuracy = 0.


Start training


In [35]:
mp_trainer = MLM(cfg, cuda=cfg['cuda'])

NameError: name 'hidden_2_dim' is not defined

In [ ]:
epochs = cfg['epochs']
for epoch in tqdm(range(cfg['epochs'] + 1)):
    if epoch > int(epochs*0.8):
        for g in mp_trainer.optim.param_groups:
            g['lr'] = g['lr']/10

#     f1_macro_test, prec_macro_test, recall_macro_test, accuracy_test = test_performance(test_loader,
#                                                                                         mp_trainer,
#                                                                                         num_of_classes = cfg['output_dimesion'])
#     f1_macro_train, prec_macro_train, recall_macro_train, accuracy_train = test_performance(train_loader,
#                                                                                             mp_trainer,
#                                                                                             num_of_classes = cfg['output_dimesion'])
#     # Save vals for test:
#     performance['acc_test'].append(accuracy_test)
#     performance['prec_test'].append(prec_macro_test)
#     performance['f1_test'].append(f1_macro_test)
#     performance['recall_test'].append(recall_macro_test)

#     # Save vals for train:
#     performance['acc_train'].append(accuracy_train)
#     performance['prec_train'].append(prec_macro_train)
#     performance['f1_train'].append(f1_macro_train)
#     performance['recall_train'].append(recall_macro_train)

#     with open(cfg['logfilename'], 'a+') as logfile:
#         logfile.write('On test we have accuracy = {}, f1 = {}, prec = {}, recall = {}\n'.format(accuracy_test,
#                                                                                                 f1_macro_test,
#                                                                                                 prec_macro_test,
#                                                                                                 recall_macro_test))
#         logfile.write('On train we have accuracy = {}, f1 = {}, prec = {}, recall = {}\n'.format(accuracy_train,
#                                                                                                 f1_macro_train,
#                                                                                                 prec_macro_train,
#                                                                                                 recall_macro_train))

#     if accuracy_test > best_accuracy:
#         mp_trainer.save(cfg['trainerfilename'])
#         with open(cfg['logfilename'], 'a+') as logfile:
#             logfile.write(
#                 'New best model with accuracy = {} saved at {}\n'.format(accuracy_test, cfg['trainerfilename']))
#         best_accuracy = accuracy_test
#     else:
#         with open(cfg['logfilename'], 'a+') as logfile:
#             logfile.write('Best model has accuracy = {}\n'.format(best_accuracy))

#     # save current performance.
#     json.dump(performance, open(repo_name + 'performance.json', 'w'))
#     # plot performance
#     visualize_performance(performance, repo_name)

    if epoch == range(cfg['epochs']):
        # It's the last epoch, don't train again.
        break

    print('Train epoch {}:'.format(epoch))
    epoch_loss = []
    for i, batch in tqdm(enumerate(train_loader)):
        loss = mp_trainer.update(batch)
        epoch_loss.append(float(loss.detach()))
        print(loss)
        if i % 50 == 0:
            with open(cfg['logfilename'], 'a+') as logfile:
                logfile.write('sample {} of {} in epoch {} of {}.\n'.format(i,
                                                                            len(train_loader),
                                                                            epoch,
                                                                            cfg['epochs']))

    #performance['loss'].append(np.mean(np.array(epoch_loss)))


In [ ]:
10,64,450

## MISC

In [211]:
for batch in test_loader:
    #print(np.shape(batch))
    print(np.shape(batch[0]))
    #print(batch[0][3][2])
    

torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])
torch.Size([20, 64, 64])


In [22]:
txt = "election on an anti-slavery platform, an initial seven slave states declared their secession from the country to form the Confederacy. War broke out in April 1861 "
        
doc = nlp(txt)

In [23]:
doc

election on an anti-slavery platform, an initial seven slave states declared their secession from the country to form the Confederacy. War broke out in April 1861 

In [24]:
(64-len(doc))

34

In [25]:
if len(doc) <64:
    txt = txt + ' PAD'*(63-len(doc))
    doc = nlp(txt)
elif len(doc) > 64:
    doc = doc[:64]

In [26]:
vocab.map([token.text for token in doc])

[9114,
 114,
 117,
 2873,
 30,
 7398,
 1,
 28,
 117,
 7540,
 6888,
 7323,
 16878,
 301,
 191,
 1,
 455,
 8,
 5943,
 6,
 3110,
 8,
 1,
 37,
 4693,
 6097,
 220,
 125,
 14842,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1]

In [27]:
[token.text for token in doc]

['election',
 'on',
 'an',
 'anti',
 '-',
 'slavery',
 'platform',
 ',',
 'an',
 'initial',
 'seven',
 'slave',
 'states',
 'declared',
 'their',
 'secession',
 'from',
 'the',
 'country',
 'to',
 'form',
 'the',
 'Confederacy',
 '.',
 'War',
 'broke',
 'out',
 'in',
 'April',
 '1861',
 ' ',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD',
 'PAD']

In [28]:
[token.pos_ for token in doc]

['NOUN',
 'ADP',
 'DET',
 'ADJ',
 'ADJ',
 'ADJ',
 'NOUN',
 'PUNCT',
 'DET',
 'ADJ',
 'NUM',
 'NOUN',
 'NOUN',
 'VERB',
 'PRON',
 'NOUN',
 'ADP',
 'DET',
 'NOUN',
 'PART',
 'VERB',
 'DET',
 'PROPN',
 'PUNCT',
 'NOUN',
 'VERB',
 'ADP',
 'ADP',
 'PROPN',
 'NUM',
 'SPACE',
 'PROPN',
 'PROPN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'NOUN',
 'PROPN',
 'PROPN',
 'PROPN']

In [29]:
[token.lemma_ for token in doc]

['election',
 'on',
 'an',
 'anti',
 '-',
 'slavery',
 'platform',
 ',',
 'an',
 'initial',
 'seven',
 'slave',
 'state',
 'declare',
 'their',
 'secession',
 'from',
 'the',
 'country',
 'to',
 'form',
 'the',
 'Confederacy',
 '.',
 'war',
 'break',
 'out',
 'in',
 'April',
 '1861',
 ' ',
 'PAD',
 'PAD',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'pad',
 'PAD',
 'PAD',
 'PAD']

In [30]:
adj, root_id = doc_to_adj(doc, directed=False, self_loop=True)

In [31]:
adj

tensor([[1., 1., 0.,  ..., 0., 0., 0.],
        [1., 1., 0.,  ..., 0., 0., 0.],
        [0., 0., 1.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 1., 0., 1.],
        [0., 0., 0.,  ..., 0., 1., 1.],
        [0., 0., 0.,  ..., 1., 1., 1.]])

In [32]:
root_id

25

# data preprocess

In [ ]:
labels = vocab.map([token.text for token in doc])

In [ ]:
inputs = vocab.map([token.text for token in doc])

In [ ]:
# create random array of floats in equal dimension to input_ids
rand = torch.rand(np.shape(vocab.map([token.text for token in doc])))
# where the random array is less than 0.15, we set true
mask_arr = rand < 0.15
mask_arr

In [ ]:
# create selection from mask_arr
selection = torch.flatten((mask_arr).nonzero()).tolist()
selection

In [ ]:
for i in selection: 
    inputs[i] = 103

In [ ]:
inputs